In [23]:
import os
import re
import glob
import pandas as pd
import numpy as np
import itertools
import torch
import random
import matplotlib.pyplot as plt
from matplotlib.path import Path
from scipy.ndimage import gaussian_filter, maximum_filter, generate_binary_structure, iterate_structure
from itertools import chain
import plotly.express as px
import plotly.graph_objects as go


from prnn.utils.predictiveNet import PredictiveNet
from prnn.utils.agent import RatInABoxAgent, RandomActionAgent
from prnn.utils.env import make_env
from prnn.utils.general import saveFig
from prnn.utils.figures import TrainingFigure
from prnn.analysis.SpatialTuningAnalysis import SpatialTuningAnalysis
from prnn.analysis.OfflineTrajectoryAnalysis import OfflineTrajectoryAnalysis
from prnn.analysis.OfflineActivityAnalysis import SpontaneousActivityAnalysis
from prnn.analysis.representationalGeometryAnalysis import representationalGeometryAnalysis
from prnn.analysis.TuningCurveAnalysis import TuningCurveAnalysis

In [24]:
print(os.getcwd())


/Users/hadrienpadilla/Documents/McGill/Peyrache Lab/pRNN


In [25]:
import pandas as pd
from pathlib import Path

data_paths = [
    "Data/hadrien_analyzed_nets/base_nets/",
    "Data/hadrien_analyzed_nets/GD_no_reward/",
    "Data/hadrien_analyzed_nets/GD_reward_mults/",
    "Data/hadrien_analyzed_nets/GD_reward_repeats/",
    "Data/hadrien_analyzed_nets/rand_rew_mult/",
    "Data/hadrien_analyzed_nets/rand_rew_repeats/",
]

dfs = []


for path in data_paths:
    category = Path(path).name  # last part of path as category
    print(f"Loading data from {path} -> category: {category}")
    pickle_files = sorted(Path(path).glob("*.pkl"))
    print(f"Found {len(pickle_files)} pickle files.")
    for f in pickle_files:
        df = pd.read_pickle(f)
        df["category"] = category
        dfs.append(df)


analysis = pd.concat(dfs, ignore_index=True)

Loading data from Data/hadrien_analyzed_nets/base_nets/ -> category: base_nets
Found 1 pickle files.
Loading data from Data/hadrien_analyzed_nets/GD_no_reward/ -> category: GD_no_reward
Found 7 pickle files.
Loading data from Data/hadrien_analyzed_nets/GD_reward_mults/ -> category: GD_reward_mults
Found 7 pickle files.
Loading data from Data/hadrien_analyzed_nets/GD_reward_repeats/ -> category: GD_reward_repeats
Found 7 pickle files.
Loading data from Data/hadrien_analyzed_nets/rand_rew_mult/ -> category: rand_rew_mult
Found 7 pickle files.
Loading data from Data/hadrien_analyzed_nets/rand_rew_repeats/ -> category: rand_rew_repeats
Found 7 pickle files.


In [26]:
analysis

netname  \
0           multRNN_5win_i2_o2-no_reward-s1042_ep5-cpu   
1      multRNN_5win_i2_o2-no_reward_1001-s1001_ep5-cpu   
2      multRNN_5win_i2_o2-no_reward_2002-s2002_ep5-cpu   
3      multRNN_5win_i2_o2-no_reward_3003-s3003_ep5-cpu   
4      multRNN_5win_i2_o2-no_reward_4004-s4004_ep5-cpu   
..                                                 ...   
205  multRNN_5win_i2_o23-repeat_150_ep5_6006-s1042_ep5   
206   multRNN_5win_i2_o23-repeat_25_ep5_6006-s1042_ep5   
207   multRNN_5win_i2_o23-repeat_50_ep5_6006-s1042_ep5   
208    multRNN_5win_i2_o23-repeat_5_ep5_6006-s1042_ep5   
209   multRNN_5win_i2_o23-repeat_75_ep5_6006-s1042_ep5   

                                                  bins  \
0    {'single': {'counts': [12, 19, 18, 26, 34, 36]...   
1    {'single': {'counts': [17, 15, 10, 29, 19, 29]...   
2    {'single': {'counts': [15, 19, 13, 33, 33, 30]...   
3    {'single': {'counts': [15, 17, 12, 34, 41, 32]...   
4    {'single': {'counts': [6, 16, 11, 21, 31, 21],...   
..                                                 ...   
205  {'single': {'counts': [10, 21, 23, 32, 16, 15]...   
206  {'single': {'counts': [10, 15, 24, 32, 17, 14]...   
207  {'single': {'counts': [10, 20, 21, 31, 16, 12]...   
208  {'single': {'counts': [15, 18, 18, 28, 17, 12]...   
209  {'single': {'counts': [10, 19, 25, 32, 17, 12]...   

                                                 cells  \
0    [{'idx': 1, 'center': [0.65625, 0.593754020718...   
1    [{'idx': 0, 'center': [0.59375, 0.343754020718...   
2    [{'idx': 1, 'center': [0.65625, 0.593754020718...   
3    [{'idx': 1, 'center': [0.53125, 0.656254020718...   
4    [{'idx': 1, 'center': [0.28125, 0.406254020718...   
..                                                 ...   
205  [{'idx': 0, 'center': [0.59375, 0.718754020718...   
206  [{'idx': 0, 'center': [0.59375, 0.656254020718...   
207  [{'idx': 0, 'center': [0.59375, 0.656254020718...   
208  [{'idx': 0, 'center': [0.59375, 0.718754020718...   
209  [{'idx': 0, 'center': [0.65625, 0.593754020718...   

                                               circles  \
0    {'single': {'counts': [0, 0, 0], 'fractions': ...   
1    {'single': {'counts': [0, 0, 0], 'fractions': ...   
2    {'single': {'counts': [0, 3, 2], 'fractions': ...   
3    {'single': {'counts': [0, 2, 2], 'fractions': ...   
4    {'single': {'counts': [0, 2, 3], 'fractions': ...   
..                                                 ...   
205  {'single': {'counts': [0, 4, 0], 'fractions': ...   
206  {'single': {'counts': [0, 5, 0], 'fractions': ...   
207  {'single': {'counts': [0, 3, 1], 'fractions': ...   
208  {'single': {'counts': [0, 5, 0], 'fractions': ...   
209  {'single': {'counts': [0, 3, 0], 'fractions': ...   

                                         complex_peaks          category  
0    [{'idx': 1, 'peaks': [(16, 15), (0, 10), (11, ...         base_nets  
1    [{'idx': 1, 'peaks': [(15, 2), (18, 12), (0, 1...         base_nets  
2    [{'idx': 1, 'peaks': [(12, 18)]}, {'idx': 4, '...         base_nets  
3    [{'idx': 1, 'peaks': []}, {'idx': 8, 'peaks': ...         base_nets  
4    [{'idx': 2, 'peaks': [(14, 11)]}, {'idx': 4, '...         base_nets  
..                                                 ...               ...  
205  [{'idx': 0, 'peaks': [(15, 9), (2, 11)]}, {'id...  rand_rew_repeats  
206  [{'idx': 0, 'peaks': [(2, 11), (14, 9)]}, {'id...  rand_rew_repeats  
207  [{'idx': 0, 'peaks': [(14, 9), (2, 11)]}, {'id...  rand_rew_repeats  
208  [{'idx': 0, 'peaks': [(1, 11), (14, 9)]}, {'id...  rand_rew_repeats  
209  [{'idx': 0, 'peaks': [(2, 11), (14, 9)]}, {'id...  rand_rew_repeats  

[210 rows x 6 columns]

In [27]:
def n_repeats(row) -> str:
    full = row['netname']
    s = full.lower()
    m = re.search(r'(repeat|multiply|multiple)[^0-9]*([0-9]+)', s)
    if m:
        kind, num = m.group(1), int(m.group(2))
        return str(num)
    else:
        return 'no reward prediction'
analysis['n_repeats'] = analysis.apply(n_repeats, axis=1)

def seed(row):
    full = row['netname']
    s = full.lower()
    if '1001' in s:
        return 1001
    elif '2002' in s:
        return 2002
    elif '3003' in s:
        return 3003
    elif '4004' in s:
        return 4004
    elif '5005' in s:
        return 5005
    elif '6006' in s:
        return 6006
    else:
        return 1042
analysis['seed'] = analysis.apply(seed, axis=1)

def bin_calc(row):
    single_fracs = row['bins']['single']['fractions']
    single = single_fracs[1] + single_fracs[2] + single_fracs[4]
    sc_fracs = row['bins']['single+complex']['fractions']
    single_complex = sc_fracs[1] + sc_fracs[2] + sc_fracs[4]
    try:
        scm_fracs = row['bins']['single+complex_mult_peaks']['fractions']
        single_complex_mult = scm_fracs[1] + scm_fracs[2] + scm_fracs[4]
    except KeyError:
        single_complex_mult = None
    return single, single_complex, single_complex_mult
analysis[['single_bins', 'single_bins_complex', 'single_bins_complex_mult']] = analysis.apply(bin_calc, axis=1, result_type='expand')

# analysis["category"] = analysis["category"].cat.rename_categories({"rand rew": "rand repeat"})

def circle_calc(row):
    single = sum(row['circles']['single']['fractions'])
    single_complex = sum(row['circles']['single+complex']['fractions'])
    try:
        single_complex_mult = sum(row['circles']['single+complex_mult_peaks']['fractions'])
    except KeyError:
        single_complex_mult = None
    return single, single_complex, single_complex_mult
analysis[['single_circles', 'single_circles_complex', 'single_circles_complex_mult']] = analysis.apply(circle_calc, axis=1, result_type='expand')

out_pkl = os.path.join('Data/hadrien_analyzed_nets/', "updatedmegaDF.pkl")
analysis.to_pickle(out_pkl)

In [28]:
def counts_within_radius(points_xy, centers_xy, radius):
    if len(centers_xy) == 0: return np.array([], dtype=int)
    if len(points_xy) == 0:  return np.zeros(len(centers_xy), dtype=int)
    diff = points_xy[None,:,:] - centers_xy[:,None,:]
    d2 = np.sum(diff*diff, axis=2)
    return np.sum(d2 <= radius**2, axis=1).astype(int)

def count_angular_bins(points_xy,
                       center=(0.6, 0.6),
                       n_slices=6,
                       start_angle=0.0,
                       radius=None):
    pts = np.asarray(points_xy, float)
    c = np.asarray(center, float)
    v = pts - c
    r = np.hypot(v[:,0], v[:,1])
    theta = (np.arctan2(v[:,1], v[:,0])- start_angle) % (2*np.pi)
    w = 2*np.pi / n_slices
    idx = np.floor(theta / w).astype(int)          # 0..n_slices-1
    counts = np.bincount(idx[idx >= 0], minlength=n_slices)
    return counts, idx

def build_bins(points_xy, *, center=(0.6,0.6), n_slices=6, start_angle=0.0, radius=0.6):
    import numpy as np

    pts = np.asarray(points_xy, float)
    if pts.size == 0:
        return {"counts": [0]*n_slices, "fractions": [0.0]*n_slices}
    if pts.ndim == 1 and pts.size == 2:
        pts = pts.reshape(1, 2)
    try:
        counts, _ = count_angular_bins(pts, center=center, n_slices=n_slices,
                                       start_angle=start_angle, radius=radius)
    except NameError:
        return None

    counts = [int(c) for c in counts]
    total = sum(counts) or 1  # avoid div-by-zero
    return {
        "counts": counts,
        "fractions": [c/total for c in counts]
    }

def build_circles(points_xy, reward_xy, *, radius=0.05):
    counts = counts_within_radius(points_xy, reward_xy, radius)
    total  = max(len(points_xy), 1)
    return {"counts":[int(c) for c in counts],
            "fractions":[float(c)/float(total) for c in counts],
            "radius": float(radius)}

def _safe_pct(nums, totals):
    """Return 100*nums/totals with NaN where totals==0 (no warnings)."""
    return np.divide(100.0 * nums, totals,
                     out=np.full_like(nums, np.nan, dtype=float),
                     where=(totals > 0))

def totals_and_pct_in_circles(df, cat):
    """
    Totals from df['bins'] (denominator), numerator from df['circles'].
    Returns (totals, pct).
    """
    totals = df["bins"].apply(lambda b: sum(b[cat]["counts"])).to_numpy()
    nums   = df["circles"].apply(lambda c: sum(c[cat]["counts"])).to_numpy()
    return totals, _safe_pct(nums, totals)

def totals_and_pct_in_bins(df, cat):
    """
    Totals and numerator from df['bins'].
    'nums' is the sum of selected reward bins (indices 0,1,3) — change if needed.
    Returns (totals, pct).
    """
    totals = df["bins"].apply(lambda b: sum(b[cat]["counts"])).to_numpy()
    nums   = df["bins"].apply(lambda b: sum(b[cat]["counts"][i] for i in (0,1,3))).to_numpy()
    return totals, _safe_pct(nums, totals)

EXTRACTORS = {
    "circles": totals_and_pct_in_circles,
    "bins":    totals_and_pct_in_bins,
}


In [29]:
def _normalize_metric(metric: str) -> str:
    m = (metric or "").strip().lower()
    return "pct" if m in {"pct", "percent", "percentage", "%"} else "totals"

def short_label(full: str) -> str:
    s = full.lower()
    if re.search(r'no[-_]?reward', s):
        return 'no_reward'
    m = re.search(r'(repeat|multiply|multiple)[^0-9]*([0-9]+)', s)
    if m:
        kind, num = m.group(1), int(m.group(2))
        return f"{'r' if kind=='repeat' else 'm'}{num}"
    return full

def order_by_repeat(labels_iterable):
    """
    Build x-order: no_reward, then r* ascending, then m* ascending.
    labels_iterable can be any iterable of short labels.
    """
    labels = set(labels_iterable)
    has_nr = "no_reward" in labels
    r_nums = sorted({int(x[1:]) for x in labels if re.fullmatch(r"r\d+", x)})
    m_nums = sorted({int(x[1:]) for x in labels if re.fullmatch(r"m\d+", x)})
    return (["no_reward"] if has_nr else []) + [f"r{n}" for n in r_nums] + [f"m{n}" for n in m_nums]

In [30]:
analysis

netname  \
0           multRNN_5win_i2_o2-no_reward-s1042_ep5-cpu   
1      multRNN_5win_i2_o2-no_reward_1001-s1001_ep5-cpu   
2      multRNN_5win_i2_o2-no_reward_2002-s2002_ep5-cpu   
3      multRNN_5win_i2_o2-no_reward_3003-s3003_ep5-cpu   
4      multRNN_5win_i2_o2-no_reward_4004-s4004_ep5-cpu   
..                                                 ...   
205  multRNN_5win_i2_o23-repeat_150_ep5_6006-s1042_ep5   
206   multRNN_5win_i2_o23-repeat_25_ep5_6006-s1042_ep5   
207   multRNN_5win_i2_o23-repeat_50_ep5_6006-s1042_ep5   
208    multRNN_5win_i2_o23-repeat_5_ep5_6006-s1042_ep5   
209   multRNN_5win_i2_o23-repeat_75_ep5_6006-s1042_ep5   

                                                  bins  \
0    {'single': {'counts': [12, 19, 18, 26, 34, 36]...   
1    {'single': {'counts': [17, 15, 10, 29, 19, 29]...   
2    {'single': {'counts': [15, 19, 13, 33, 33, 30]...   
3    {'single': {'counts': [15, 17, 12, 34, 41, 32]...   
4    {'single': {'counts': [6, 16, 11, 21, 31, 21],...   
..                                                 ...   
205  {'single': {'counts': [10, 21, 23, 32, 16, 15]...   
206  {'single': {'counts': [10, 15, 24, 32, 17, 14]...   
207  {'single': {'counts': [10, 20, 21, 31, 16, 12]...   
208  {'single': {'counts': [15, 18, 18, 28, 17, 12]...   
209  {'single': {'counts': [10, 19, 25, 32, 17, 12]...   

                                                 cells  \
0    [{'idx': 1, 'center': [0.65625, 0.593754020718...   
1    [{'idx': 0, 'center': [0.59375, 0.343754020718...   
2    [{'idx': 1, 'center': [0.65625, 0.593754020718...   
3    [{'idx': 1, 'center': [0.53125, 0.656254020718...   
4    [{'idx': 1, 'center': [0.28125, 0.406254020718...   
..                                                 ...   
205  [{'idx': 0, 'center': [0.59375, 0.718754020718...   
206  [{'idx': 0, 'center': [0.59375, 0.656254020718...   
207  [{'idx': 0, 'center': [0.59375, 0.656254020718...   
208  [{'idx': 0, 'center': [0.59375, 0.718754020718...   
209  [{'idx': 0, 'center': [0.65625, 0.593754020718...   

                                               circles  \
0    {'single': {'counts': [0, 0, 0], 'fractions': ...   
1    {'single': {'counts': [0, 0, 0], 'fractions': ...   
2    {'single': {'counts': [0, 3, 2], 'fractions': ...   
3    {'single': {'counts': [0, 2, 2], 'fractions': ...   
4    {'single': {'counts': [0, 2, 3], 'fractions': ...   
..                                                 ...   
205  {'single': {'counts': [0, 4, 0], 'fractions': ...   
206  {'single': {'counts': [0, 5, 0], 'fractions': ...   
207  {'single': {'counts': [0, 3, 1], 'fractions': ...   
208  {'single': {'counts': [0, 5, 0], 'fractions': ...   
209  {'single': {'counts': [0, 3, 0], 'fractions': ...   

                                         complex_peaks          category  \
0    [{'idx': 1, 'peaks': [(16, 15), (0, 10), (11, ...         base_nets   
1    [{'idx': 1, 'peaks': [(15, 2), (18, 12), (0, 1...         base_nets   
2    [{'idx': 1, 'peaks': [(12, 18)]}, {'idx': 4, '...         base_nets   
3    [{'idx': 1, 'peaks': []}, {'idx': 8, 'peaks': ...         base_nets   
4    [{'idx': 2, 'peaks': [(14, 11)]}, {'idx': 4, '...         base_nets   
..                                                 ...               ...   
205  [{'idx': 0, 'peaks': [(15, 9), (2, 11)]}, {'id...  rand_rew_repeats   
206  [{'idx': 0, 'peaks': [(2, 11), (14, 9)]}, {'id...  rand_rew_repeats   
207  [{'idx': 0, 'peaks': [(14, 9), (2, 11)]}, {'id...  rand_rew_repeats   
208  [{'idx': 0, 'peaks': [(1, 11), (14, 9)]}, {'id...  rand_rew_repeats   
209  [{'idx': 0, 'peaks': [(2, 11), (14, 9)]}, {'id...  rand_rew_repeats   

                n_repeats  seed  single_bins  single_bins_complex  \
0    no reward prediction  1042     0.489655             0.501109   
1    no reward prediction  1001     0.369748             0.413953   
2    no reward prediction  2002     0.454545             0.455782   
3    no reward prediction  3003     0.463576             0.471366   
4

In [25]:
#   TABLE BUILD
def build_long_table(
    dfs_by_seed,
    *,
    source="circles",           # "circles" or "bins"
    cat="single+complex",
    metric="pct",               # "pct" or "totals"
    include_base=False,
    base_df=None,
    base_label="base"
):
    if not dfs_by_seed:
        raise ValueError("dfs_by_seed is empty")
    if source not in EXTRACTORS:
        raise ValueError(f"source must be one of {list(EXTRACTORS)}, got {source!r}")
    metric = _normalize_metric(metric)
    extractor = EXTRACTORS[source]

    # Build x-axis order from ALL seeds (robust to mixed r*/m*/no_reward across seeds)
    labels_all = []
    for df_ in dfs_by_seed:
        if not {"netname", "bins", "circles"}.issubset(df_.columns):
            raise KeyError("Each dataframe must have columns: 'netname', 'bins', 'circles'")
        labels_all.extend(short_label(s) for s in df_["netname"])
    short_order = order_by_repeat(labels_all)

    rows = []
    for s_idx, df_seed in enumerate(dfs_by_seed, start=1):
        totals, pct = extractor(df_seed, cat)
        vals = pct if metric == "pct" else totals
        for cond, val in zip(df_seed["netname"], vals):
            rows.append({
                "condition": cond,
                "cond_short": short_label(cond),
                "full_name": cond,
                "value": val,
                "seed": f"seed_{s_idx}",
            })

        if include_base:
            if base_df is None or len(base_df) != 1:
                raise ValueError("include_base=True requires base_df with exactly one row.")
            b_totals, b_pct = extractor(base_df, cat)
            b_val = b_pct[0] if metric == "pct" else b_totals[0]
            rows.append({
                "condition": base_label,
                "cond_short": base_label,
                "full_name": "BASE: " + base_label,
                "value": b_val,
                "seed": f"seed_{s_idx}",
            })

    data = pd.DataFrame(rows)
    if include_base and base_label not in short_order:
        short_order.append(base_label)
    return data, short_order

def make_box_with_seed_lines(
    dfs_by_seed,
    *,
    source="circles",           # "circles" or "bins"
    cat="single+complex",
    metric="pct",               # "pct" or "totals"
    include_base=False,
    base_df=None,
    base_label="base",
    title=None
):
    data, short_order = build_long_table(
        dfs_by_seed, source=source, cat=cat, metric=metric,
        include_base=include_base, base_df=base_df, base_label=base_label
    )

    metric = _normalize_metric(metric)

    # 1) Box layer (no scatter in this trace to avoid double plotting)
    fig = px.box(
        data, x="cond_short", y="value",
        category_orders={"cond_short": short_order},
        template="plotly_white"
    )
    for tr in fig.data:
        if tr.type == "box":
            tr.boxmean = True
            tr.showlegend = False
            tr.hovertemplate = "%{x}: %{y:.2f}<extra></extra>"

    # 2) Seed lines (points connected across conditions)
    for seed_name, df_seed_points in data.groupby("seed", sort=False):
        # d = (df_seed_points
        #      .set_index("cond_short")
        #      .reindex(short_order)   # align to x-order
        #      .reset_index()
        #      .dropna(subset=["value"]))  # drop missing for this seed
        order = pd.CategoricalDtype(categories=short_order, ordered=True)
        d = (df_seed_points[df_seed_points['cond_short'].isin(short_order)]
            .assign(cond_short=pd.Categorical(df_seed_points['cond_short'], dtype=order))
            .sort_values('cond_short')
            .dropna(subset=['value']))
        fig.add_trace(go.Scatter(
            x=d["cond_short"], y=d["value"],
            mode="lines+markers",
            name=seed_name,
            customdata=d["full_name"],
            hovertemplate="%{x}: %{y:.2f}<br>%{customdata}<extra></extra>",
            line=dict(width=1.5),
            marker=dict(size=7, opacity=0.85)
        ))

    # 3) Titles / axes
    y_title = "Percent" if metric == "pct" else "Total counts"
    src_tag = f" ({source})"
    full_title = title or f"{cat} — {y_title}{src_tag}"
    if metric == "pct":
        y_title = "Percent" if source == "circles" else "Percent (bins-based %)"

    fig.update_layout(
        title=full_title,
        xaxis_title="Condition",
        yaxis_title=y_title,
        boxmode="group",
        legend_title_text="Seed",
        margin=dict(l=50, r=20, t=60, b=60)
    )
    fig.update_xaxes(tickangle=0)
    return fig

In [ ]:
def create_boxplot(df, category_col='category', categories=['base', 'gd mult'],
                                   value_col='single_bins', box_col='n_repeats'):
    """
    Create boxplot comparing two categories across seeds
    Parameters:
    - df: DataFrame containing the data
    - category_col: column name containing categories
    - value_col: column name with values to plot (i.e. 'single_bins')
    - box_col: column name containing grouping information
    """
    # Filter for only 'base' and 'gd mult' categories
    filtered_df = df[df[category_col].isin(categories)].copy()
    if filtered_df.empty:
        print("No data found for 'base' and 'gd mult' categories")
        return None
    # Create the boxplot
    # fig = px.box(
    #     filtered_df,
    #     x=box_col,
    #     y=value_col,
    #     category_orders={box_col: ['no reward prediction', '5', '10', '25', '50', '75', '100', '150']},
    #     color=box_col,
    #     title=f"{value_col}: {categories[0]} vs {categories[1]}",
    #     labels={
    #         box_col: f"{box_col}",
    #         value_col: f"{value_col}",
    #         box_col: f"{box_col}"
    #     },
    #     template="plotly_white"
    # )

    #using this to color by category instead of box_col
    fig = px.box(
        filtered_df,
        x=box_col,
        y=value_col,
        color=category_col,
        category_orders={box_col: ['no reward prediction', '5', '10', '25', '50', '75', '100', '150']},
        color_discrete_map={categories[0]: "#1f77b4", categories[1]: "#ff7f0e"},
        title=f"{value_col}: {categories[0]} vs {categories[1]}",
        labels={box_col: f"{box_col}", value_col: f"{value_col}"},
        template="plotly_white"
    )
    # Update layout for better readability
    fig.update_layout(
        boxmode='group',
        xaxis_title="Multiplicator",
        yaxis_title=f"{value_col}",
        legend_title="Multiplicator",
        margin=dict(l=50, r=20, t=60, b=60)
    )
    # Add mean markers to boxes
    for trace in fig.data:
        if trace.type == 'box':
            trace.boxmean = True
    return fig

In [33]:
analysis

netname  \
0           multRNN_5win_i2_o2-no_reward-s1042_ep5-cpu   
1      multRNN_5win_i2_o2-no_reward_1001-s1001_ep5-cpu   
2      multRNN_5win_i2_o2-no_reward_2002-s2002_ep5-cpu   
3      multRNN_5win_i2_o2-no_reward_3003-s3003_ep5-cpu   
4      multRNN_5win_i2_o2-no_reward_4004-s4004_ep5-cpu   
..                                                 ...   
205  multRNN_5win_i2_o23-repeat_150_ep5_6006-s1042_ep5   
206   multRNN_5win_i2_o23-repeat_25_ep5_6006-s1042_ep5   
207   multRNN_5win_i2_o23-repeat_50_ep5_6006-s1042_ep5   
208    multRNN_5win_i2_o23-repeat_5_ep5_6006-s1042_ep5   
209   multRNN_5win_i2_o23-repeat_75_ep5_6006-s1042_ep5   

                                                  bins  \
0    {'single': {'counts': [12, 19, 18, 26, 34, 36]...   
1    {'single': {'counts': [17, 15, 10, 29, 19, 29]...   
2    {'single': {'counts': [15, 19, 13, 33, 33, 30]...   
3    {'single': {'counts': [15, 17, 12, 34, 41, 32]...   
4    {'single': {'counts': [6, 16, 11, 21, 31, 21],...   
..                                                 ...   
205  {'single': {'counts': [10, 21, 23, 32, 16, 15]...   
206  {'single': {'counts': [10, 15, 24, 32, 17, 14]...   
207  {'single': {'counts': [10, 20, 21, 31, 16, 12]...   
208  {'single': {'counts': [15, 18, 18, 28, 17, 12]...   
209  {'single': {'counts': [10, 19, 25, 32, 17, 12]...   

                                                 cells  \
0    [{'idx': 1, 'center': [0.65625, 0.593754020718...   
1    [{'idx': 0, 'center': [0.59375, 0.343754020718...   
2    [{'idx': 1, 'center': [0.65625, 0.593754020718...   
3    [{'idx': 1, 'center': [0.53125, 0.656254020718...   
4    [{'idx': 1, 'center': [0.28125, 0.406254020718...   
..                                                 ...   
205  [{'idx': 0, 'center': [0.59375, 0.718754020718...   
206  [{'idx': 0, 'center': [0.59375, 0.656254020718...   
207  [{'idx': 0, 'center': [0.59375, 0.656254020718...   
208  [{'idx': 0, 'center': [0.59375, 0.718754020718...   
209  [{'idx': 0, 'center': [0.65625, 0.593754020718...   

                                               circles  \
0    {'single': {'counts': [0, 0, 0], 'fractions': ...   
1    {'single': {'counts': [0, 0, 0], 'fractions': ...   
2    {'single': {'counts': [0, 3, 2], 'fractions': ...   
3    {'single': {'counts': [0, 2, 2], 'fractions': ...   
4    {'single': {'counts': [0, 2, 3], 'fractions': ...   
..                                                 ...   
205  {'single': {'counts': [0, 4, 0], 'fractions': ...   
206  {'single': {'counts': [0, 5, 0], 'fractions': ...   
207  {'single': {'counts': [0, 3, 1], 'fractions': ...   
208  {'single': {'counts': [0, 5, 0], 'fractions': ...   
209  {'single': {'counts': [0, 3, 0], 'fractions': ...   

                                         complex_peaks          category  \
0    [{'idx': 1, 'peaks': [(16, 15), (0, 10), (11, ...         base_nets   
1    [{'idx': 1, 'peaks': [(15, 2), (18, 12), (0, 1...         base_nets   
2    [{'idx': 1, 'peaks': [(12, 18)]}, {'idx': 4, '...         base_nets   
3    [{'idx': 1, 'peaks': []}, {'idx': 8, 'peaks': ...         base_nets   
4    [{'idx': 2, 'peaks': [(14, 11)]}, {'idx': 4, '...         base_nets   
..                                                 ...               ...   
205  [{'idx': 0, 'peaks': [(15, 9), (2, 11)]}, {'id...  rand_rew_repeats   
206  [{'idx': 0, 'peaks': [(2, 11), (14, 9)]}, {'id...  rand_rew_repeats   
207  [{'idx': 0, 'peaks': [(14, 9), (2, 11)]}, {'id...  rand_rew_repeats   
208  [{'idx': 0, 'peaks': [(1, 11), (14, 9)]}, {'id...  rand_rew_repeats   
209  [{'idx': 0, 'peaks': [(2, 11), (14, 9)]}, {'id...  rand_rew_repeats   

                n_repeats  seed  single_bins  single_bins_complex  \
0    no reward prediction  1042     0.489655             0.501109   
1    no reward prediction  1001     0.369748             0.413953   
2    no reward prediction  2002     0.454545             0.455782   
3    no reward prediction  3003     0.463576             0.471366   
4

In [40]:
create_boxplot(analysis, categories=['GD_reward_mults', 'rand_rew_mult', 'base_nets', 'GD_no_reward', 'GD_reward_repeats', 'rand_rew_repeats'])